##### Pipeline for Generating Time Series Burn scar datasets for GFM Bench (outside of USA) 
In this pipeline, we use the `pre and post fire images   to define a "year" for generating the time series, generate 4 images during that event year, and use the same range of months in previous years to sample for control years. We ensure that the event year has a sample after the date of the post fire image.

In [1]:
import os
os.chdir("../")
os.environ["CPL_VSIL_CURL_NUM_CONNECTIONS"] = "20"

In [2]:
import yaml
from datetime import datetime, timedelta
import calendar

import pystac
import pystac_client
import planetary_computer
import stackstac 
from pystac_client.stac_api_io import StacApiIO
from urllib3 import Retry
from requests.adapters import HTTPAdapter
import dask.distributed
import numpy as np
import pandas as pd
import geopandas as gpd
import matplotlib.pyplot as plt
import xarray as xr
import rioxarray
from dask.distributed import Client, LocalCluster

from rasterio.features import rasterize
from shapely.geometry import mapping
from shapely.wkt import loads
from scipy.signal import convolve2d
from scipy.ndimage import uniform_filter
from shapely.geometry import shape
import os, planetary_computer as pc, rasterio
from rasterio.errors import RasterioIOError
from tenacity import retry, wait_random_exponential, stop_after_attempt

import stackstac, dask.array as da

from src.utils import (search_s2_scenes, 
                       stack_s2_data, 
                       unique_class, 
                       missing_values, 
                       gen_chips, 
                       mask_cloudy_pixels
)
import warnings
warnings.filterwarnings("ignore")

In [3]:
with open("config.yml", "r") as file:
    config = yaml.safe_load(file)

In [4]:
# utility functions
def add_start_date(event_id):
    start_date = pd.to_datetime(event_id[-8:], format="%Y%m%d")
    return start_date

def add_pre_date(pre_id):
    if len(pre_id)<=15:
        pre_date = pd.to_datetime(pre_id[-8:], format="%Y%m%d")
    else:
        pre_date = pd.to_datetime(pre_id.split("_")[0][-8:], format="%Y%m%d")

    return pre_date

def add_post_date(post_id):
    if len(post_id)<=15:
        post_date = pd.to_datetime(post_id[-8:], format="%Y%m%d")
    else:
        post_date = pd.to_datetime(post_id.split("_")[0][-8:], format="%Y%m%d")

    return post_date

def get_fire_mask_path(fire_df):
    df_filtered = fire_df[fire_df["event_type"].isin(["pre", "post"])]
    summary = (
        df_filtered
        .groupby("location")
        .agg(
            geometry=("geometry", "first"),
            pre_date=("date", lambda x: sorted(x[df_filtered.loc[x.index, "event_type"] == "pre"])[0] if any(df_filtered.loc[x.index, "event_type"] == "pre") else None),
            post_date=("date", lambda x: sorted(x[df_filtered.loc[x.index, "event_type"] == "post"])[0] if any(df_filtered.loc[x.index, "event_type"] == "post") else None),
        )
        .reset_index()
    )

    if isinstance(summary["geometry"].iloc[0], str):
        summary["geometry"] = summary["geometry"].apply(loads)
    summary_gdf = gpd.GeoDataFrame(summary, geometry=summary["geometry"], crs="EPSG:4326")
    summary_gdf["pre_date"] = pd.to_datetime(summary_gdf["pre_date"])
    summary_gdf["post_date"] = pd.to_datetime(summary_gdf["post_date"])

    mask_paths = (
        fire_df[fire_df["event_type"] == "mask"]
        .groupby("location")["path"]
        .first()  #one fire mask per location
        .reset_index()

        .rename(columns={"path": "mask_path"})
    )
    summary_gdf = summary_gdf.merge(mask_paths, on="location", how="left")
    return summary_gdf

def quarter_window(year, start_m, end_m):
    """Return a 'YYYY-MM-DD/YYYY-MM-DD' string for a single quarter."""
    start = f"{year}-{start_m:02d}-01"
    end_day = calendar.monthrange(year, end_m)[1]
    end   = f"{year}-{end_m:02d}-{end_day:02d}"
    return f"{start}/{end}"

def get_date_ranges(row, n_control_years: int = 7):
    # 4 chips PER event year (calendar not seasons)
    # 4 for for each control year (depending on the availability of Sentinel-2 data)
    post_date   = pd.to_datetime(row["post_date"])
    event_year  = post_date.year
    quarters = [(1, 3), (4, 6), (7, 9), (10, 12)]

    event_ranges = [ # Event-year ranges (always 4)
        quarter_window(event_year, sm, em) for sm, em in quarters
    ]
    
    # control-year ranges
    control_ranges = []
    for delta in range(1, n_control_years + 1):
        cy = event_year - delta
        control_ranges.append([
            quarter_window(cy, sm, em) for sm, em in quarters
        ])
    return event_ranges, control_ranges

def rasterize_aoi(aoi, s2_stack):
    """
    Rasterize the AOI polygon into a burn mask
    """
    aoi_gdf = gpd.GeoDataFrame(
        {"geometry": [shape(aoi['geometry'])]},
        crs="EPSG:4326"
    )
    
    aoi_proj = aoi_gdf.to_crs(s2_stack.rio.crs)
    
    burn_mask = rasterize(
        [(mapping(aoi_proj['geometry'].iloc[0]), 1)],
        out_shape=(s2_stack.sizes['y'], s2_stack.sizes['x']),
        transform=s2_stack.rio.transform(),
        fill=0,
        dtype='uint8'
    )
    
    burn_mask_da = xr.DataArray(
        burn_mask,
        coords={"y": s2_stack["y"], "x": s2_stack["x"]},
        dims=("y", "x")
    )
    return burn_mask_da

def crop_burn_windows(s2_stack, burn_mask, chip_size=224, pct_threshold=0.30):
    """
    Return *all* windows of size `chip_size`×`chip_size` whose burn-pixel
    fraction is ≥ `pct_threshold`.

    Returns
    -------
    list[xr.DataArray]  each element is a cropped stack
    """
    step = chip_size        # non-overlap; set <chip_size for stride/overlap
    ny, nx = burn_mask.shape
    chips = []

    for y0 in range(0, ny - chip_size + 1, step):
        for x0 in range(0, nx - chip_size + 1, step):
            window = burn_mask[y0:y0+chip_size, x0:x0+chip_size]
            frac   = window.mean()        # fraction of burn pixels in the window
            if frac >= pct_threshold:     # keep only “burn-rich” windows
                chips.append(
                    s2_stack.isel(
                        y=slice(y0, y0+chip_size),
                        x=slice(x0, x0+chip_size),
                        drop=False
                    )
                )
    return chips

def harmonize_to_old(data):
    """
    Harmonize new Sentinel-2 data to the old baseline.

    Parameters
    ----------
    data: xarray.DataArray
        A DataArray with four dimensions: time, band, y, x

    Returns
    -------
    harmonized: xarray.DataArray
        A DataArray with all values harmonized to the old
        processing baseline.
    """
    if "time" not in data.dims:
        # static composite --> nothing to do
        return data
    if "time" not in data.dims:
        if "time" in data:
            data = data.expand_dims("time")  # convert scalar to 1D dimension
        else:
            raise ValueError("Variable 'time' not found in dataset.")
            
    data = data.set_index(time="time")

    cutoff = datetime(2022, 1, 25)
    offset = 1000
    bands = [
        "B01",
        "B02",
        "B03",
        "B04",
        "B05",
        "B06",
        "B07",
        "B08",
        "B8A",
        "B09",
        "B10",
        "B11",
        "B12",
    ]

    old = data.sel(time=slice(cutoff))

    to_process = list(set(bands) & set(data.band.data.tolist()))
    new = data.sel(time=slice(cutoff, None)).drop_sel(band=to_process)

    new_harmonized = data.sel(time=slice(cutoff, None), band=to_process).clip(offset)
    new_harmonized -= offset

    new = xr.concat([new, new_harmonized], "band").sel(band=data.band.data.tolist())
    
    return xr.concat([old, new], dim="time")

def search_s2_scenes(aoi, date_range, catalog, config, best_one=True):
    search = catalog.search(
        collections=["sentinel-2-l2a"],
        bbox=aoi.geometry.bounds,
        datetime=date_range,
        query=[f"s2:nodata_pixel_percentage<{config["sentinel_2"]["nodata_pixel_percentage"]}",
                 f"eo:cloud_cover<{config["sentinel_2"]["cloud_cover"]}"
                ],
        limit=None,                     
    )
    items = list(search.get_items())

    if best_one and items:
        items = [min(items, key=lambda it: it.properties["eo:cloud_cover"])]

    return pystac.ItemCollection(items)

def generate_fire_chips(s2_stack, aoi, config, time_series_type, epsg, index, metadata_df):
    saved_any = False
    try:
        s2_stack = s2_stack.compute()
    except:
        print("skipping the AOI for no S2 data")
    if s2_stack.shape[2] != 224 or s2_stack.shape[3] != 224:
        print(f"Skipping chip ID {index} for mismatch dimensions")
        return False, metadata_df 
    
    for crop_idx, s2_stack_cropped in enumerate(s2_stack):
        if "time" not in s2_stack_cropped.dims:
            if "time" in s2_stack_cropped.coords:
                s2_stack_cropped = s2_stack_cropped.expand_dims("time")
            else:
                print(f"Skipping chip ID {index} — no time dimension present")
                continue
        if missing_values(s2_stack_cropped, config['chips']['chip_size'], config['chips']['chip_size']):
            print(f"Skipping chip ID {index} for missing values")
            continue      
                
        s2_stack_cropped = harmonize_to_old(s2_stack_cropped)
    
        s2_stack_cropped = s2_stack_cropped.fillna(-999)
        s2_stack_cropped = s2_stack_cropped.rio.write_nodata(-999)
        s2_stack_cropped = s2_stack_cropped.astype(np.dtype(np.int16))
        s2_stack_cropped = s2_stack_cropped.rename("s2")

        if time_series_type == "event":
            for dt in s2_stack_cropped.time.values:
                print(f"Processing chip ID {index} for event date {dt}")
                ts = pd.to_datetime(str(dt)) 
                s2_path = f"data/fire_data_v5/s2_{index:08}.tif"
                if os.path.exists(s2_path):
                    print(f"Skipping chip ID {index}_{crop_idx} for chip {index} date: {ts.strftime('%Y%m%d')} — file already exists")
                    continue
                print(f"Saving chip ID {index}_{crop_idx} for chip {index} date: {ts.strftime('%Y%m%d')}")
                s2_stack_cropped.sel(time=dt).squeeze().rio.to_raster(s2_path)

                metadata_df = pd.concat([pd.DataFrame([[index,
                                                        ts.strftime('%Y%m%d'),
                                                        f"{index:08}",
                                                        "event",
                                                        f"{aoi["source"]}",
                                                        f"{aoi["pre_date"]}",
                                                        f"{aoi["post_date"]}",
                                                        s2_stack_cropped.x[int(len(s2_stack_cropped.x)/2)].data,
                                                        s2_stack_cropped.y[int(len(s2_stack_cropped.y)/2)].data,
                                                        epsg]
                                                    ],
                                                    columns=metadata_df.columns
                                                    ),
                                        metadata_df],
                                        ignore_index=True
                                    )
                saved_any = True
        else:
            for dt in s2_stack_cropped.time.values:
                print(f"Processing chip ID {index} for control date {dt}")
                ts = pd.to_datetime(str(dt)) 
                s2_path = f"data/fire_data_v5/s2_{index:08}.tif"
                if os.path.exists(s2_path):
                    print(f"Skipping chip ID {index}_{crop_idx} for chip {index} date: {ts.strftime('%Y%m%d')} — file already exists")
                    continue
                print(f"Saving chip ID {index}_{crop_idx} for chip {index} date: {ts.strftime('%Y%m%d')}")
                s2_stack_cropped.sel(time = dt).squeeze().rio.to_raster(s2_path)
                metadata_df = pd.concat([pd.DataFrame([[index,
                                                        ts.strftime('%Y%m%d'),
                                                        f"{index:08}",
                                                        "control",
                                                        f"{aoi["source"]}",
                                                        f"{aoi["pre_date"]}",
                                                        f"{aoi["post_date"]}",
                                                        s2_stack_cropped.x[int(len(s2_stack_cropped.x)/2)].data,
                                                        s2_stack_cropped.y[int(len(s2_stack_cropped.y)/2)].data,
                                                        epsg]
                                                    ],
                                            columns=metadata_df.columns
                                            ),
                                metadata_df],
                                ignore_index=True
                            )
                saved_any = True
    return saved_any, metadata_df


@retry(wait=wait_random_exponential(max=30), stop=stop_after_attempt(4))
def _open_once(href):
    with rasterio.open(href):
        pass

def build_stack(items, aoi_geom, cfg, epsg):
    # wrapper around stackstac + masking 
    if not items:
        return None
    try:
        for it in items:
            planetary_computer.sign_inplace(it)
        first_band = cfg["sentinel_2"]["bands"][0]
        _open_once(items[0].assets[first_band].href)
        stack = stackstac.stack(
            items,
            assets=cfg["sentinel_2"]["bands"],
            epsg=epsg,
            resolution=cfg["sentinel_2"]["resolution"],
            fill_value=np.nan,
            bounds_latlon=aoi_geom.bounds,
        )
        stack = mask_cloudy_pixels(stack).drop_sel(band="SCL")
        return stack
    except Exception as e:
        print(f"Error stacking S2 data: {e}")
        return None

def collect_event_chips(stack, burn_mask, cfg):
    """Return list[(chip_stack, (y0,y1,x0,x1))] filtered by pct-burn."""
    chip_slices = []
    for y0 in range(0, burn_mask.shape[0] - cfg["chips"]["chip_size"] + 1,
                   cfg["chips"]["chip_size"]):
        for x0 in range(0, burn_mask.shape[1] - cfg["chips"]["chip_size"] + 1,
                       cfg["chips"]["chip_size"]):
            window = burn_mask[y0:y0 + cfg["chips"]["chip_size"],
                               x0:x0 + cfg["chips"]["chip_size"]]
            if window.mean() >= 0.30:
                chip_slices.append((y0, y0 + cfg["chips"]["chip_size"],
                                    x0, x0 + cfg["chips"]["chip_size"]))

    chips = [
        (stack.isel(y=slice(y0, y1), x=slice(x0, x1), drop=False),
         (y0, y1, x0, x1))
        for y0, y1, x0, x1 in chip_slices
    ]
    return chips


In [5]:
# load s2wcd fire events data
fire_df = pd.read_csv("data/s2_wcd_fires.csv")
fire_gpd = gpd.GeoDataFrame(fire_df.copy())
fire_gpd.set_geometry(fire_gpd["geometry"].apply(loads), inplace=True)
fire_gpd.set_crs("EPSG:4326", inplace=True)
# fire_gpd.head()

summary_gdf = get_fire_mask_path(fire_df)
summary_gdf["source"] = "S2 WCD"
summary_gdf.head()

location                                           geometry   pre_date  \
0   Almonaster  MULTIPOLYGON (((-1.94651 41.37228, -1.94652 41... 2022-07-12   
1       Attica  MULTIPOLYGON (((23.2936 38.09311, 23.2936 38.0... 2021-08-16   
2  Australia_1  POLYGON ((116.09595 -31.70046, 116.09595 -31.7... 2021-01-31   
3  Australia_2  MULTIPOLYGON (((116.0803 -31.75746, 116.08009 ... 2021-01-31   
4        Bejis  MULTIPOLYGON (((-0.71135 39.88491, -0.71147 39... 2022-08-08   

   post_date                                          mask_path  source  
0 2022-07-27  /workspace/Rufai/data/S2-WCD/Almonaster/cm/cm.tif  S2 WCD  
1 2021-08-28      /workspace/Rufai/data/S2-WCD/Attica/cm/cm.tif  S2 WCD  
2 2021-02-20  /workspace/Rufai/data/S2-WCD/Australia_1/cm/cm...  S2 WCD  
3 2021-02-20  /workspace/Rufai/data/S2-WCD/Australia_2/cm/cm...  S2 WCD  
4 2022-08-23       /workspace/Rufai/data/S2-WCD/Bejis/cm/cm.tif  S2 WCD

In [6]:
mtbs_gdf = gpd.read_file("data/mtbs/mtbs_perims_DD.shp")
mtbs_gdf["start_date"] = mtbs_gdf["Event_ID"].apply(add_start_date)
selected_mtbs_fires = mtbs_gdf
selected_mtbs_fires = selected_mtbs_fires[selected_mtbs_fires["Incid_Type"].isin(["Wildfire"])] #, "Prescribed Fire"
selected_mtbs_fires = selected_mtbs_fires[selected_mtbs_fires["Comment"].isnull()]
selected_mtbs_fires = selected_mtbs_fires[~selected_mtbs_fires["Pre_ID"].isnull()]
selected_mtbs_fires = selected_mtbs_fires[~selected_mtbs_fires["Post_ID"].isnull()]
selected_mtbs_fires = selected_mtbs_fires[selected_mtbs_fires["start_date"]>pd.to_datetime("20210101", format="%Y%m%d")]
selected_mtbs_fires["location"] = selected_mtbs_fires["Incid_Name"]
selected_mtbs_fires["source"] = selected_mtbs_fires["Map_Prog"]
selected_mtbs_fires = selected_mtbs_fires[selected_mtbs_fires["start_date"]<pd.to_datetime("20240101", format="%Y%m%d")]
selected_mtbs_fires["pre_date"] = selected_mtbs_fires["Pre_ID"].apply(add_pre_date)
selected_mtbs_fires["post_date"] = selected_mtbs_fires["Post_ID"].apply(add_post_date)
# len(selected_mtbs_fires)
selected_mtbs_fires.head()

Event_ID                               irwinID  \
17161  NJ3973407472120220619  400501E0-C028-41BA-BF7E-189BFAA0F876   
17163  NC3565607641720220619  FF845212-7195-428F-88B5-1E904EA26003   
17165  FL2576508042220220329  CFBFE97D-0AAB-4777-89DB-6C5AE68BA263   
17166  FL2632608099820220328  07627D47-33EE-40C9-8773-DF8DDCF4D748   
17168  FL2540408046920220426  C8F015EF-F5A2-402A-BF64-6D89D8A7ECAB   

               Incid_Name Incid_Type    Map_ID Map_Prog Asmnt_Type  BurnBndAc  \
17161  MULLICA RIVER FIRE   Wildfire  10024293     MTBS    Initial      13082   
17163        FEREBEE ROAD   Wildfire  10024302     MTBS    Initial       1954   
17165             137 AVE   Wildfire  10024307     MTBS    Initial        857   
17166         INTERCEPTOR   Wildfire  10024309     MTBS    Initial       4143   
17168     125 MILE MARKER   Wildfire  10024312     MTBS    Initial        830   

      BurnBndLat BurnBndLon  ... Low_T Mod_T High_T Comment  \
17161     39.689    -74.681  ...    30   306    600    None   
17163     35.673    -76.427  ...    50  9999   9999    None   
17165     25.769    -80.433  ...    50   450   9999    None   
17166     26.297    -81.059  ...    50  9999   9999    None   
17168     25.411    -80.479  ...    50  9999   9999    None   

                                                geometry  start_date  \
17161  POLYGON ((-74.69252 39.68403, -74.6923 39.6837...  2022-06-19   
17163  POLYGON ((-76.42425 35.65565, -76.42447 35.654...  2022-06-19   
17165  POLYGON ((-80.43589 25.77237, -80.43507 25.772...  2022-03-29   
17166  POLYGON ((-81.08343 26.29129, -81.08347 26.291...  2022-03-28   
17168  POLYGON ((-80.48006 25.41823, -80.48017 25.417...  2022-04-26   

                 location  source   pre_date  post_date  
17161  MULLICA RIVER FIRE    MTBS 2021-06-07 2022-07-04  
17163        FEREBEE ROAD    MTBS 2021-07-25 2022-07-20  
17165             137 AVE    MTBS 2022-03-26 2022-04-10  
17166         INTERCEPTOR    MTBS 2022-03-26 2022-04-10  
17168     125 MILE MARKER    MTBS 2020-05-05 2022-05-25  

[5 rows x 28 columns]

In [7]:
merged_df = summary_gdf.merge(
    selected_mtbs_fires, 
    on=["geometry", "pre_date", "post_date", 'location', 'source'],
    how="outer"
)
merged_df = merged_df[[c for c in 
                       ['source',
                        'location',
                        "geometry",
                        # "pre_date",
                        # "post_date",
                        ] if c in merged_df.columns]]
print("Number of fire events:", len(merged_df))

Number of fire events: 786


### Load datasets from STAC API

In [8]:
cluster = LocalCluster()
client = Client(cluster)
print(client.dashboard_link)

http://127.0.0.1:8787/status


2025-08-28 22:19:02,932 - distributed.scheduler - WARNING - Detected different `run_spec` for key ('fetch_raster_window-b74d35acfbbac435fa761c5c57936eaa', 0, 0, 1, 1) between two consecutive calls to `update_graph`. This can cause failures and deadlocks down the line. Please ensure unique key names. If you are using a standard dask collections, consider releasing all the data before resubmitting another computation. More details and help can be found at https://github.com/dask/dask/issues/9888. 
Debugging information
---------------------
old task state: waiting
old run_spec: (<function execute_task at 0x7fe6fc1fb060>, (('asset_table_to_reader_and_window-fetch_raster_window-b74d35acfbbac435fa761c5c57936eaa', 0, 0, 1, 1),), {})
new run_spec: (subgraph_callable-4c72d78e26230c395b1f644921e95a82, (('asset_table_to_reader_and_window-a3f9aaa5f503655d3a07c92b3f777103', 0, 0), (slice(1024, 2048, None), slice(1024, 2048, None)), dtype('float64'), nan), {})
old token: ('tuple', (('913ceb5b5beb46

In [9]:
retry = Retry(
    total=10, backoff_factor=1, status_forcelist=[502, 503, 504], allowed_methods=None
)
stac_api_io = StacApiIO(max_retries=retry)
catalog = pystac_client.Client.open(
    "https://planetarycomputer.microsoft.com/api/stac/v1",
    modifier=planetary_computer.sign_inplace,
    stac_io=stac_api_io
)

In [10]:
metadata_df = pd.DataFrame(columns=["chip_id", "date", "sample_id", "type", "source", "pre_date", "post_date" "x_center", "y_center", "epsg"])
# metadata_df = pd.read_csv("data/metadata_df.csv")

In [ ]:
for index, aoi in merged_df.iterrows():
    index= index+1
    print(f"\nProcessing AOI {index:02d}")
    # if index <= 879:
    #     continue

    event_date_ranges, control_date_ranges = get_date_ranges(aoi, n_control_years=7)

    # Use all 4 event scenes to extract event stacks
    event_stacks = []
    for q_idx, dr in enumerate(event_date_ranges):
        s2_items = search_s2_scenes(aoi, dr, catalog, config, best_one=True)
        if len(s2_items) == 0:
            event_stacks = None
            break
        epsg = (s2_items[0].properties.get("proj:epsg") or
                int(s2_items[0].properties["proj:code"].split(":")[-1]))
        stack = build_stack(s2_items, aoi.geometry, config, epsg)
        if stack is None or len(stack.time) != 1:
            event_stacks = None
            break
        event_stacks.append((stack, epsg))

    if event_stacks is None or len(event_stacks) != 4:
        print("Incomplete event stacks — skipping AOI")
        continue

    #Collect shared burn-rich chip slices from Q1 (use as base)
    burn_mask_q1 = rasterize_aoi(aoi, event_stacks[0][0])
    base_chip_slices = collect_event_chips(event_stacks[0][0], burn_mask_q1, config)
    print(f"Found {len(base_chip_slices)} burn-rich chip areas")

    for chip_id_num, (chip_da_q1, chip_slice) in enumerate(base_chip_slices):
        y0, y1, x0, x1 = chip_slice
        event_chip_valid = True
        chip_quarter_data = []

        for q_idx, (stack, epsg) in enumerate(event_stacks):
            chip = stack.isel(y=slice(y0, y1), x=slice(x0, x1), drop=False)
            try:
                chip = chip.compute()
            except:
                event_chip_valid = False
                break

            if chip.shape[2:] != (224, 224):
                event_chip_valid = False
                break
            if missing_values(chip, 224, 224):
                event_chip_valid = False
                break

            chip_quarter_data.append((chip, epsg, q_idx))

        if not event_chip_valid or len(chip_quarter_data) != 4:
            print(f"Skipping chip slice {chip_id_num} — not valid for all 4 quarters")
            continue

        # Save event chips for all 4 quarters
        for chip, epsg, q_idx in chip_quarter_data:
            dt = pd.to_datetime(str(chip.time.values[0]))
            date_str = dt.strftime('%Y%m%d')
            chip_id = f"{index:05d}_{chip_id_num:02d}_e_Q{q_idx+1}_{date_str}"
            out_path = f"data/fire_data_v5/s2_{chip_id}.tif"

            if os.path.exists(out_path):
                print(f"  Event chip exists: {chip_id}")
            else:
                print(f"  Saving event chip: {chip_id}")
                saved, metadata_df = generate_fire_chips(
                    chip, aoi, config, "event", epsg, chip_id, metadata_df
                )

        # CONTROL YEARS — replicate for each valid chip slice
        for ctrl_year_idx, ctrl_ranges in enumerate(control_date_ranges):
            ctrl_chip_quarters = []
            control_valid = True

            for q_idx, dr in enumerate(ctrl_ranges):
                s2_ctrl_items = search_s2_scenes(aoi, dr, catalog, config, best_one=True)
                if len(s2_ctrl_items) == 0:
                    control_valid = False
                    break

                ctrl_epsg = (s2_ctrl_items[0].properties.get("proj:epsg") or
                             int(s2_ctrl_items[0].properties["proj:code"].split(":")[-1]))
                ctrl_stack = build_stack(s2_ctrl_items, aoi.geometry, config, ctrl_epsg)
                if ctrl_stack is None or len(ctrl_stack.time) != 1:
                    control_valid = False
                    break

                ctrl_chip = ctrl_stack.isel(y=slice(y0, y1), x=slice(x0, x1), drop=False)
                try:
                    ctrl_chip = ctrl_chip.compute()
                except:
                    control_valid = False
                    break

                if ctrl_chip.shape[2:] != (224, 224):
                    control_valid = False
                    break
                if missing_values(ctrl_chip, 224, 224):
                    control_valid = False
                    break

                ctrl_chip_quarters.append((ctrl_chip, ctrl_epsg, q_idx))

            # if not control_valid or len(ctrl_chip_quarters) != 4:
            #     print(f"  Skipping control year {ctrl_year_idx+1} for chip {chip_id_num}")
            #     continue

            # Save control chips for this chip slice
            for ctrl_chip, ctrl_epsg, q_idx in ctrl_chip_quarters:
                dt = pd.to_datetime(str(ctrl_chip.time.values[0]))
                date_str = dt.strftime('%Y%m%d')
                ctrl_chip_id = f"{index:05d}_{chip_id_num:02d}_c_Q{q_idx+1}_{date_str}"
                out_path = f"data/fire_data_v5/s2_{ctrl_chip_id}.tif"

                if os.path.exists(out_path):
                    print(f"  Control chip exists: {ctrl_chip_id}")
                else:
                    print(f"  Saving control chip: {ctrl_chip_id}")
                    saved, metadata_df = generate_fire_chips(
                        ctrl_chip, aoi, config, "control", ctrl_epsg, ctrl_chip_id, metadata_df
                    )

    metadata_df.to_csv("data/metadata_df.csv", index=False)



Processing AOI 01
Found 6 burn-rich chip areas
  Saving event chip: 00001_00_e_Q1_20210312
Processing chip ID 00001_00_e_Q1_20210312 for event date 2021-03-12T17:51:31.024000000
Saving chip ID 00001_00_e_Q1_20210312_0 for chip 00001_00_e_Q1_20210312 date: 20210312
  Saving event chip: 00001_00_e_Q2_20210630
Processing chip ID 00001_00_e_Q2_20210630 for event date 2021-06-30T17:49:11.024000000
Saving chip ID 00001_00_e_Q2_20210630_0 for chip 00001_00_e_Q2_20210630 date: 20210630
  Saving event chip: 00001_00_e_Q3_20210809
Processing chip ID 00001_00_e_Q3_20210809 for event date 2021-08-09T17:49:11.024000000
Saving chip ID 00001_00_e_Q3_20210809_0 for chip 00001_00_e_Q3_20210809 date: 20210809
  Saving event chip: 00001_00_e_Q4_20211003
Processing chip ID 00001_00_e_Q4_20211003 for event date 2021-10-03T17:50:59.024000000
Saving chip ID 00001_00_e_Q4_20211003_0 for chip 00001_00_e_Q4_20211003 date: 20211003
Skipping chip slice 1 — not valid for all 4 quarters
Skipping chip slice 2 — not

2025-08-28 20:27:14,328 - distributed.worker - ERROR - Compute Failed
Key:       ('fetch_raster_window-f01da2fd7bbcedf20fd15ddbd8f0b171', 0, 1, 1, 0)
State:     executing
Function:  subgraph_callable-514c0ced276fe7697b168c991c0fe1f9
args:      (array([[(<stackstac.rio_reader.AutoParallelRioReader object at 0x7f94bc1600b0>, Window(col_off=-3475.2067791922454, row_off=-7953.214921158913, width=11568.012856088477, height=11567.377421674028))]],
      dtype=object), (slice(1024, 1447, None), slice(0, 1024, None)), dtype('float64'), nan)
kwargs:    {}
Exception: 'RuntimeError("Error reading Window(col_off=0, row_off=1024, width=1024, height=423) from \'https://sentinel2l2a01.blob.core.windows.net/sentinel2-l2/12/S/YC/2023/12/17/S2A_MSIL2A_20231217T175741_N0510_R141_T12SYC_20231220T075048.SAFE/GRANULE/L2A_T12SYC_A044325_20231217T175740/IMG_DATA/R10m/T12SYC_20231217T175741_B03_10m.tif?st=2025-08-27T19%3A35%3A51Z&se=2025-08-28T20%3A20%3A51Z&sp=rl&sv=2025-07-05&sr=c&skoid=9c8ff44a-6a2c-4dfb-b29

Skipping chip slice 18 — not valid for all 4 quarters


2025-08-28 20:27:14,838 - distributed.worker - ERROR - Compute Failed
Key:       ('fetch_raster_window-b5b10f2036cf7412199b123da39c0e6a', 0, 0, 0, 1)
State:     executing
Function:  subgraph_callable-da2e5527854f820979b4c3d8c73f3772
args:      (array([[(<stackstac.rio_reader.AutoParallelRioReader object at 0x7f94c51ad460>, Window(col_off=-3475.1849701538886, row_off=-7953.2166700740345, width=11568.04442509498, height=11567.378715963685))]],
      dtype=object), (slice(0, 1024, None), slice(1024, 1866, None)), dtype('float64'), nan)
kwargs:    {}
Exception: 'RuntimeError("Error opening \'https://sentinel2l2a01.blob.core.windows.net/sentinel2-l2/12/S/YC/2023/01/26/S2B_MSIL2A_20230126T175619_N0400_R141_T12SYC_20230127T232238.SAFE/GRANULE/L2A_T12SYC_A030769_20230126T175849/IMG_DATA/R10m/T12SYC_20230126T175619_B02_10m.tif?st=2025-08-27T19%3A35%3A51Z&se=2025-08-28T20%3A20%3A51Z&sp=rl&sv=2025-07-05&sr=c&skoid=9c8ff44a-6a2c-4dfb-b298-1c9212f64d9a&sktid=72f988bf-86f1-41af-91ab-2d7cd011db47&skt

Skipping chip slice 19 — not valid for all 4 quarters


...

Skipping chip slice 79 — not valid for all 4 quarters


2025-08-29 15:41:12,574 - distributed.worker - ERROR - Compute Failed
Key:       ('asset_table_to_reader_and_window-fetch_raster_window-cb1d31f842389b3f3a3c2025158ebeb9', 0, 4, 3, 1)
State:     executing
Function:  execute_task
args:      ((subgraph_callable-1e472a31cada129ed73bcc77f8856ca6, (subgraph_callable-7f7685061078a8dbb830e22922c5a29a, array([[('https://sentinel2l2a01.blob.core.windows.net/sentinel2-l2/11/S/PU/2023/03/31/S2A_MSIL2A_20230331T181921_N0509_R127_T11SPU_20230401T023700.SAFE/GRANULE/L2A_T11SPU_A040593_20230331T183331/IMG_DATA/R20m/T11SPU_20230331T181921_B11_20m.tif?st=2025-08-28T14%3A52%3A36Z&se=2025-08-29T15%3A37%3A36Z&sp=rl&sv=2025-07-05&sr=c&skoid=9c8ff44a-6a2c-4dfb-b298-1c9212f64d9a&sktid=72f988bf-86f1-41af-91ab-2d7cd011db47&skt=2025-08-29T10%3A00%3A46Z&ske=2025-09-05T10%3A00%3A46Z&sks=b&skv=2025-07-05&sig=%2BpPWfSlYsX1pWgrS/UHY3GWLsFpultj7Osu7LG3lwqc%3D', [ 598813.38878328, 3788386.5196718 ,  712316.48081749, 3901881.90139113], [1., 0.])]],
      dtype=[('url', 

Skipping chip slice 80 — not valid for all 4 quarters


2025-08-29 15:41:12,844 - distributed.worker - ERROR - Compute Failed
Key:       ('asset_table_to_reader_and_window-fetch_raster_window-cb1d31f842389b3f3a3c2025158ebeb9', 0, 2, 3, 1)
State:     executing
Function:  execute_task
args:      ((subgraph_callable-1e472a31cada129ed73bcc77f8856ca6, (subgraph_callable-7f7685061078a8dbb830e22922c5a29a, array([[('https://sentinel2l2a01.blob.core.windows.net/sentinel2-l2/11/S/PU/2023/03/31/S2A_MSIL2A_20230331T181921_N0509_R127_T11SPU_20230401T023700.SAFE/GRANULE/L2A_T11SPU_A040593_20230331T183331/IMG_DATA/R10m/T11SPU_20230331T181921_B04_10m.tif?st=2025-08-28T14%3A52%3A36Z&se=2025-08-29T15%3A37%3A36Z&sp=rl&sv=2025-07-05&sr=c&skoid=9c8ff44a-6a2c-4dfb-b298-1c9212f64d9a&sktid=72f988bf-86f1-41af-91ab-2d7cd011db47&skt=2025-08-29T10%3A00%3A46Z&ske=2025-09-05T10%3A00%3A46Z&sks=b&skv=2025-07-05&sig=%2BpPWfSlYsX1pWgrS/UHY3GWLsFpultj7Osu7LG3lwqc%3D', [ 598813.38878328, 3788386.5196718 ,  712316.48081749, 3901881.90139113], [1., 0.])]],
      dtype=[('url', 

Skipping chip slice 81 — not valid for all 4 quarters

Processing AOI 242
Found 13 burn-rich chip areas
  Saving event chip: 00242_00_e_Q1_20210205
Processing chip ID 00242_00_e_Q1_20210205 for event date 2021-02-05T17:55:29.024000000
Saving chip ID 00242_00_e_Q1_20210205_0 for chip 00242_00_e_Q1_20210205 date: 20210205
  Saving event chip: 00242_00_e_Q2_20210516
Processing chip ID 00242_00_e_Q2_20210516 for event date 2021-05-16T17:49:09.024000000
Saving chip ID 00242_00_e_Q2_20210516_0 for chip 00242_00_e_Q2_20210516 date: 20210516
  Saving event chip: 00242_00_e_Q3_20210710
Processing chip ID 00242_00_e_Q3_20210710 for event date 2021-07-10T17:49:11.024000000
Saving chip ID 00242_00_e_Q3_20210710_0 for chip 00242_00_e_Q3_20210710 date: 20210710
  Saving event chip: 00242_00_e_Q4_20211112
Processing chip ID 00242_00_e_Q4_20211112 for event date 2021-11-12T17:55:59.024000000
Saving chip ID 00242_00_e_Q4_20211112_0 for chip 00242_00_e_Q4_20211112 date: 20211112
  Saving control chip: 0